# Marknadsanalys av diamanter


# Innehållsförteckning

### 1. Introduktion
- 1.1 Inledning  
- 1.2 Diamantens värdering  
- 1.3 Mål och syfte  
- 1.4 Metod  

### 2. Databearbetning
- 2.1 Inläsning av data  
- 2.2 Datacleanse  
- 2.3 Datacleanse – summering och förklaringar  
- 2.4 Datacleanse – resultat  

### 3. GIA & Cut-mappning
- 3.1 GIA och Cut-Mapping  

### 4. Översiktsanalys
- 4.1 Överblick  
- 4.2 Överblick – summering  
- 4.3 Selektering för skandinavisk marknad  
- 4.4 Skandinavisk marknad – summering  

### 5. Fördjupad analys
- 5.1 Fördjupning av data  
- 5.2 Fördjupning – förtydligande  
- 5.3 Fördjupning med värderingsindex  
- 5.4 Värderingsindex – visualisering  
- 5.5 Topp 50 – mest prisvärda diamanter  

### 6. Sammanfattning
- 6.1 Executive Summary  








 
## 1.1 Inledning

### Guldfynds inköpsavdelning har under en tid haft svårt att hitta ädelstenar som blir rätt prissatta ut till handeln. Detta har lett till sviktande marginaler. Denna analys är ett jobb beställt av Guldfynd och ska presenteras utav deras Sourcing Manager till ledningsgruppen.

#### I denna analys kommer vi att titta på diamanter – världens kanske mest eftertraktade ädelsten.

## 1.2 Diamantens värdering
Diamantpriser påverkas av flera faktorer: vikt (carat), slipning (cut), färg (color) och klarhet (clarity). Dessa egenskaper påverkar inte bara stenens utseende utan också dess marknadsvärde. Det är därför avgörande för Guldfynd att förstå vilka kombinationer av dessa egenskaper som erbjuder bäst **värde för pengarna**, snarare än att enbart köpa in det som är "bäst" på pappret.

## 1.3 Mål och syfte 
Den här analysen syftar till att:
- Identifiera **vilka diamantsegment som ger hög kvalitet till ett rimligt pris**.
- Ge **konkreta rekommendationer** till inköpschefen om vilka stenar som bör prioriteras.
- Tydliggöra **prisdrivande faktorer**, samt visa var företaget kan hitta **potentiella marginalfördelar**.

Målet är alltså att ge Guldfynd ett **beslutsunderlag** som bidrar till bättre affärsmässighet i inköpen, högre marginaler och en konkurrenskraftig produktportfölj.

Analysen utgår ifrån ett större dataset med över 54 000 diamanter, där varje rad representerar en unik sten med olika egenskaper och ett noterat marknadsvärde.

## 1.4 Metod  
- Rensning av orimliga/saknade värden  
- Visualisering av samband mellan carat, pris, färg, klarhet och slipning  
- Segmentering i två grupper: små (0.2–0.75 ct) och större (0.76–1.5 ct)  
- Beräkning av ett **Value Index (carat/price)**  
- Urval av de 50 mest prisvärda stenarna 



## 2.1 Inläsning och rensning av data
- I detta avsnittt läser vi in datasetet diamonds.csv i våran notebook. Vi listar hur många rader och vad det är för datatyper i setet.
- Vi importerar också våra tredjepartsbibliotek Pandas, Numpy och Plotly.

In [2]:
import pandas as pd
import numpy as np
import plotly.express as px

#Läser in dataset
df = pd.read_csv("diamonds.csv")

#längd på dataframe
length_df = len(df)
print(f'Dataset length: {length_df}')

#information om datatyper och columner
df.info()



Dataset length: 53940
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 53940 entries, 0 to 53939
Data columns (total 11 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   Unnamed: 0  53940 non-null  int64  
 1   carat       53918 non-null  float64
 2   cut         53939 non-null  object 
 3   color       53936 non-null  object 
 4   clarity     53910 non-null  object 
 5   depth       53934 non-null  float64
 6   table       53935 non-null  float64
 7   price       53928 non-null  float64
 8   x           53937 non-null  float64
 9   y           53936 non-null  float64
 10  z           53937 non-null  float64
dtypes: float64(7), int64(1), object(3)
memory usage: 4.5+ MB


## 2.2 Data cleanse
#### I detta avsnitt nedan så gör vi en funktion för att sortera och göra en data-cleanse på datasetet.


In [3]:
from pandas.api.types import CategoricalDtype

def clean_diamond_data(df):
    total_start = df.shape[0]
    removed = {}

    if 'index' not in df.columns:
        df.reset_index(inplace=True)

    before = df.shape[0]
    df = df.dropna(subset=['index', 'cut', 'color', 'clarity', 'price', 'carat', 'x', 'y', 'z', 'depth'])
    removed["Saknade värden"] = before - df.shape[0]

    
    numeric_cols = ['carat', 'depth', 'table', 'price', 'x', 'y', 'z']
    before = df.shape[0]
    for col in numeric_cols:
        df = df[df[col] > 0]
    removed["Nollvärden i numeriska kolumner"] = before - df.shape[0]

   
    before = df.shape[0]
    df = df[(df['x'] <= 15) & (df['y'] <= 15) & (df['z'] <= 15)]
    removed["Extrema mått (>15 mm)"] = before - df.shape[0]

    
    before = df.shape[0]
    df = df[~((df['carat'] < 1) & (df['z'] > 10))]
    removed["Misstänkt djup (carat < 1 & z > 10)"] = before - df.shape[0]

    
    df['depth_calc'] = (df['z'] / ((df['x'] + df['y']) / 2)) * 100
    df['depth_diff'] = abs(df['depth_calc'] - df['depth'])
    before = df.shape[0]
    df = df[df['depth_diff'] <= 0.5]
    removed[">0.5% avvikelse i depth"] = before - df.shape[0]

   
    df.drop(columns=["depth_calc", "depth_diff"], inplace=True)

    df['index'] = df['index'].astype(int)

   
    df = df.reset_index(drop=True)

    df.dropna()

    print("🧹 Sammanställning av borttagna rader:")
    for reason, quant in removed.items():
        print(f"- {reason}: {quant} rader")

    total_borttagna = total_start - df.shape[0]
    print(f"\nTotalt borttagna rader: {total_borttagna}")
    print(f"✅ Rader kvar efter rensning: {df.shape[0]}")

    return df

df = clean_diamond_data(df)

🧹 Sammanställning av borttagna rader:
- Saknade värden: 74 rader
- Nollvärden i numeriska kolumner: 22 rader
- Extrema mått (>15 mm): 3 rader
- Misstänkt djup (carat < 1 & z > 10): 0 rader
- >0.5% avvikelse i depth: 150 rader

Totalt borttagna rader: 249
✅ Rader kvar efter rensning: 53691


## 2.3 Datacleanse – Förutsättning för en tillförlitlig analys

Innan vi påbörjar någon analys av diamantdata behöver vi säkerställa att datan vi arbetar med är **komplett, rimlig och representativ** för verkliga köpbeslut. Rådata innehåller ofta saknade värden, felaktiga inmatningar och orimliga mått – allt detta kan snedvrida analysresultaten och därmed leda till felaktiga rekommendationer.

###  Vad gör `clean_diamond_data()`?

Funktionen `clean_diamond_data(df)` genomför en noggrann rensning av datan i flera steg:

1. **Tar bort rader med saknade värden** i kritiska kolumner som vikt (carat), mått (x, y, z), slipning (cut), färg, klarhet och pris.
2. **Filtrerar bort rader där numeriska värden är noll eller negativa**, vilket inte är fysiskt möjligt för ädelstenar.
3. **Tar bort extrema mått** där någon av längd, bredd eller djup överstiger 15 mm. Detta identifierar outliers som inte speglar kommersiellt gångbara diamanter.
4. **Tar bort orimliga kombinationer** såsom små stenar (carat < 1) med mycket stor höjd (z > 10 mm), vilket ofta kan indikera felregistrering av datan.
5. **Jämför uppmätt djup med beräknat geometriskt djup** och tillåter endast en avvikelse på max ±1%. Detta är ett kvalitetsfilter som upptäcker inkonsekventa inmatningar.
6. **Konverterar kvalitativa egenskaper** som `cut`, `color` och `clarity` till ordnade kategorier. Detta gör visualiseringar och gruppanalyser mer begripliga och meningsfulla.

### 2.4  Vad visar resultatet?

Efter rensningen skrivs en sammanställning ut i konsolen som visar:

- Hur många rader som tagits bort i varje steg
- Totalt antal borttagna rader
- Hur många rader som återstår i den slutgiltiga, städade datamängden

Detta gör rensningen **transparent och spårbar**, vilket är viktigt för att ledningen ska kunna förstå och lita på analysens grunddata.

Den städade datan kan nu användas för att identifiera lönsamma diamantsegment utan att störas av felaktigheter eller extremvärden.


## 3.1 Anpassning till GIA – Cut Mapping

I vårt dataset ser vi slipkvaliteter som "Ideal", "Premium", "Very Good" etc. Dessa används ofta av återförsäljare eller icke-certifierade aktörer och tenderar att vara mer generösa i sin bedömning än GIA:s formella skala.

För att göra vår analys mer realistisk och jämförbar med GIA-certifikat har vi därför översatt dessa till GIA-standard enligt följande:

| Datasetets värde | GIA-standard     |
|------------------|------------------|
| Ideal            | Excellent         |
| Premium          | Very Good         |
| Very Good        | Good              |
| Good             | Fair              |
| Fair             | Poor              |

Syftet är att inte överskatta kvaliteten på diamanterna i vår analys. Detta gör resultaten mer användbara för faktiska inköpsbeslut, där certifikat ofta krävs.



I nästa avsnitt ska vi mappa om alla datasetets värden till GIA standard med python-kod

In [7]:
cut_mapping = {
    "Ideal": "Excellent",
    "Premium": "Very Good",
    "Very Good": "Good",
    "Good": "Fair",
    "Fair": "Poor"
}

df['cut_mapped'] = df['cut'].map(cut_mapping)

cut_order_gia = ['Poor', 'Fair', 'Good', 'Very Good', 'Excellent']
df['cut_mapped'] = df['cut_mapped'].astype(CategoricalDtype(categories=cut_order_gia, ordered=True))

## 4.1 Överblick
#### I detta avsnittet ska vi skapa en visuell överblick över hur priset är fördelat på de olika stenarna

In [5]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go

fig = make_subplots(rows=1, cols=2, subplot_titles=("Pris vs Carat", "Histogram över Carat"))


fig.add_trace(
    go.Scatter(
        x=df["carat"],
        y=df["price"],
        mode='markers',
        marker=dict(color='royalblue', opacity=0.6, size=3),
        name='Pris vs Carat'
    ),
    row=1, col=1
)


fig.add_trace(
    go.Histogram(
        x=df["carat"],
        nbinsx=30,
        marker_color='mediumturquoise',
        name='Histogram Carat'
    ),
    row=1, col=2
)


fig.update_layout(
    title_text="Diamantdata: Pris och Carat",
    showlegend=False,
    height=500,
    width=1000,
    plot_bgcolor='white'
)


fig.update_xaxes(showgrid=True, gridcolor='lightgray')
fig.update_yaxes(showgrid=True, gridcolor='lightgray')

fig.show()


## 4.2 Summering överblick

### Vad vi ser

I de två översiktsdiagrammen framgår det tydligt att majoriteten av diamanterna i datasetet väger under 1 carat. Detta bekräftas i histogrammet till höger, där de flesta observationerna är koncentrerade i de lägre caratintervallen. Distributionen är tydligt snedfördelad åt höger, vilket innebär att större diamanter är ovanligare.

Scatterplotten visar relationen mellan pris och carat. Det finns ett tydligt positivt samband mellan dessa två variabler – priset ökar generellt med ökad vikt. 

Vi kan även se att vid vissa specifika viktgränser, såsom **1.0, 1.5 och 2.0 carat**, tenderar priserna att vara både högre och mer utspridda jämfört med närliggande caratnivåer. 

### Varför detta görs

Syftet med dessa visualiseringar är att snabbt få en **överblick över hur diamanterna i datamängden är fördelade**, samt att identifiera **grundläggande samband och avvikelser**. Detta ger värdefull insikt både för:

- **Analytiker**, som vill skapa modeller för prissättning eller efterfrågeprognoser
- **Beslutsfattare**, som vill förstå vilka typer av diamanter som är vanligast och vilka som driver upp priset

### Nästa steg

I nästa steg ska jag presentera data över stenar med karat som används i smycken med störst volym på den Skandinaviska marknaden.

## 4.3 Selektering av stenar för Skandinavisk marknad

In [6]:
df_filtered = df[(df['carat'] >= 0.25) & (df['carat'] <=1.5)]

fig3 = px.scatter(df_filtered,
                  x ='carat',
                  y ='price', 
                  title = 'Pris vs Karat (0.25 till 1.00 ct)',
                  color='cut',
                  labels={'carat': "Carat", 'price': "Price"})

fig4 = px.histogram(df_filtered,
                    x='carat',
                    nbins=30,
                    title='Antal diamanter i intervallet 0.25-1.00 ct',
                    labels={'carat': "Carat", 'count': "Antal"},
                    color_discrete_sequence=['mediumturquoise'])

fig_combined = make_subplots(rows=1, cols = 2,
                             subplot_titles=("Pris vs Carat", "Antal Diamanter per Carat"),
                             column_widths=[0.5,0.5])

fig_combined.add_trace(fig3['data'][0],row=1,col=1)
for trace in fig4['data']:
    fig_combined.add_trace(trace, row=1, col=2)

fig_combined.update_layout(height=500, width=1000, showlegend=False)
fig_combined.show()



## 4.4 Skandinavisk marknad, summering

### Vad vi ser
I scatter-diagrammet till vänster ser vi att diamantens pris ökar tydligt med carat-vikten inom intervallet 0.25–1.00 ct. Speciellt nära 1.00 ct syns en koncentration av både fler observationer och högre prisvariation, vilket indikerar ett psykologiskt eller marknadsmässigt tröskelvärde.

I histogrammet till höger framgår att de vanligaste carat-vikterna i detta intervall är 0.3 ct, 0.4 ct och runt 0.7 ct. Dessa toppar representerar troligen populära storlekar i smyckesproduktion, särskilt inom förlovnings- och vigselringar i Skandinavien.

### Varför görs detta
Syftet är att analysera de vanligaste och mest efterfrågade diamantvikterna inom ett relevant urval (0.25–1.00 ct), vilket är vanligt i smyckesindustrin. Genom att koppla detta till prisdata kan vi dra slutsatser om marknadsbeteenden, prissättning och potentiella kundpreferenser.

### Rekommendationer
* Fokusera på inköp och lager av diamanter i storlekarna 0.3–0.75 ct, då dessa verkar ha både hög efterfrågan och hanterbara priser.

* Undvik att göra inköp av stenar med cirka 1.00 ct utan prisanalys av segmentet, eftersom dessa ser ut att innebära en parabolisk prisökning, vilket i sin tur kan leda till marginalsänkning.

### Nästa steg 
Analysera vidare om prisvariationer vid 0.2 och upp till 1.5 ct beror på slipkvalitet, färg eller klarhet för att optimera värde för kund och marginal.



# 5.1 Fördjupning av data

I detta avsnitt ska vi minska ner scopet och dela in våra diamanter i två grupper. En med carat mellan 0.1 till 0.75 och den andra gruppen 0.76 till 1.5ct.
Vi tar också fram en scatterplot för lite visualisering.

In [ ]:

df_filtered = df[((df['carat'] >= 0.1) & (df['carat'] <= 0.75)) | 
                 ((df['carat'] >= 0.76) & (df['carat'] <= 1.5))]


df_filtered["size_group"] = df_filtered["carat"].apply(lambda x: "0.2–0.75 ct" if x <= 0.75 else "0.76–1.5 ct")


fig1 = px.scatter(df_filtered,
              x="carat",
              y="price",
              color="size_group",
              title="Prisvariation efter carat, minskad skala till 0.2 till 1.5ct",
              labels={"cut": "Slipkvalitet", "price": "Pris (USD)", "size_group": "Carat-grupp"})

fig1.show()

/var/folders/w3/_fr5m5_x717cxnsv2bczt3d40000gq/T/ipykernel_1948/1827331877.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_filtered["size_group"] = df_filtered["carat"].apply(lambda x: "0.2–0.75 ct" if x <= 0.75 else "0.76–1.5 ct")


# 5.2 Fördjupning, förtydligande

### Vad vi ser

I scatterploten över diamantdatasetet kan vi se att priset är relativt jämnt för diamanter med karatvärde mellan 0.2 och cirka 0.9. När vi når 1 karat och över, ökar prisets spridning markant. Till exempel har diamanter på 1 karat priser som sträcker sig från cirka 1600 till 16000, vilket visar en betydligt större volatilitet och variation i pris. Här får vi ha i åtanke att vi har inte tagit slipning, klarhet eller färg i beaktning.

### Varför detta görs

Syftet med denna visualisering är att förstå hur priset på diamanter varierar i relation till deras storlek (karat). Genom att identifiera var priset är relativt stabilt och var det blir mer volatilt kan vi bättre analysera marknadens dynamik och identifiera potentiella prismönster eller segment.

### Rekommendationer

* Fokusera på att noggrant analysera diamanter över 1 karat eftersom prisvariationen är stor, vilket kan påverka både prissättning och lagerhantering.
* Överväg att segmentera marknaden efter karatstorlek för att bättre rikta marknadsföring och försäljning.
* Vid inköp, var extra noggrann med kvalitetsparametrar som klarhet och slipning, då de sannolikt påverkar priset mer kraftigt vid högre karat.


## 5.3 Fördjupning med värderingsindex

I detta avsnitt ska vi visualisera en plot där vi kan betygsätta stenarnas värde per carat med ett index.
Indexet beräknas med slipning, färg och klarhet som utmappas till numeriska värden där 1 motsvarar lägst på skalan, t.ex 'Fair' eller 'I1'.

Uträkningen görs enligt följande:

värdeindex = ((slipning + färg + klarhet) / 3) / (pris/carat)

In [ ]:

df_val = df_filtered.copy()


cut_map = {'Fair': 1, 'Good': 2, 'Very Good': 3, 'Premium': 4, 'Ideal': 5}
color_map = {'J': 1, 'I': 2, 'H': 3, 'G': 4, 'F': 5, 'E': 6, 'D': 7}
clarity_map = {'I1': 1, 'SI2': 2, 'SI1': 3, 'VS2': 4, 'VS1': 5, 'VVS2': 6, 'VVS1': 7, 'IF': 8}

df_val['cut_score'] = df_val['cut'].map(cut_map)
df_val['color_score'] = df_val['color'].map(color_map)
df_val['clarity_score'] = df_val['clarity'].map(clarity_map)


df_val['value_index'] = ((df_val['cut_score'] + df_val['color_score'] + df_val['clarity_score']) / 3) / (df_val['price'] / df_val['carat'])


fig1 = px.scatter(df_val,
                  x='carat',
                  y='value_index',
                  color='cut',
                  title='Value Index vs Carat',
                  labels={'value_index': 'Value Index (kvalitet / pris per carat)', 'carat': 'Carat'})


fig2 = px.scatter(df_val,
                  x='carat',
                  y='price',
                  color='value_index',
                  color_continuous_scale='Viridis',
                  title='Pris vs Carat färgat efter Value Index',
                  labels={'price': 'Pris (USD)', 'carat': 'Carat', 'value_index': 'Value Index'})

fig1.show()
fig2.show()

48476


# 5.4 Värderingsindex, resultat av visualisering

###  Vad vi ser

I den första scatterploten (**Value Index vs Carat**) ser vi tydligt att diamanter med lägre carat generellt har ett högre **Value Index**, vilket innebär bättre kvalitet per pris-enhet. Det finns flera diamanter under 0.75 ct som ligger högt på skalan, särskilt bland slipkvaliteter som *Ideal* och *Premium*.

I den andra visualiseringen (**Pris vs Carat färgat efter Value Index**) kan vi bekräfta att:

- Priset stiger kraftigt med ökad carat.
- Högre value index (ljusare färg) koncentreras i det lägre carat-intervallet.

###  Varför detta görs

Syftet med denna analys är att identifiera **mest prisvärda diamanter** i spannet 0.2–1.5 carat. Istället för att bara fokusera på pris eller kvalitet, så kombinerar vi flera parametrar (slipning, färg, klarhet och pris per carat) för att uppskatta **"värde för pengarna"**.

Detta hjälper oss att:

- Identifiera "guldkorn" i datan.
- Förstå hur kvalitet påverkar prisbilden beroende på carat.
- Kunna göra mer säkra rekommendationer vid inköp.

###  Rekommendationer

- **Fokusera på diamanter under ~0.75 carat** för bästa värde per krona – där finns många med högt Value Index.
- **Kombinera ideal/premium-slipning med hög färg och klarhet**, men prioritera value index istället för bara absolut kvalitet.
- Använd detta värdeindex som underlag vid sourcing.


# 5.5 Top 50
I detta avsnitt ska vi ta fram en tabell med de 50 diamanter med högst värdeindex.

In [ ]:
import plotly.graph_objects as go

# Sortera och välj de 50 mest prisvärda diamanterna
top_50_df = df_val.sort_values(by="value_index", ascending=False).head(50)
top_50_df.rename(columns={"Unnamed: 0": "stone_id"}, inplace=True)
# Välj relevanta kolumner att visa
columns_to_show = ["stone_id","carat", "price", "cut", "color", "clarity", "value_index"]

# Skapa en tabell med plotly
fig = go.Figure(data=[go.Table(
    header=dict(values=[col.upper() for col in columns_to_show],
                fill_color='paleturquoise',
                align='left'),
    cells=dict(values=[top_50_df[col] for col in columns_to_show],
               fill_color='lavender',
               align='left'))
])

fig.update_layout(title="💎 Topp 50 mest prisvärda diamanter (Value Index)")
fig.show()


48476


## 5.6 Executive Summary

Denna analys syftar till att ge beslutsunderlag för att identifiera de mest prisvärda diamanterna mellan 0.2 och 1.5 carat – ett vanligt spann inom den skandinaviska smyckesmarknaden. Genom data cleansing och djupanalys har vi filtrerat ut de 50 diamanter som erbjuder bäst "value for money", beräknat som vikt i förhållande till pris (carat/price-index).

Resultaten visar att stenar runt 0.3–0.7 carat ofta ger högst värde, särskilt med slipkvaliteter som “Very Good” och “Premium”. Priset tenderar att öka oproportionerligt vid gränsen runt 1.0 ct, vilket gör mindre stenar strategiskt attraktiva för både återförsäljare och konsumenter med fokus på värdeoptimering.

Affärsrekommendationer:

Fokusera inköp på diamanter i spannet 0.3–0.7 ct med hög slipkvalitet.

Undvik marginellt större stenar som värderas högt utan ökade kvalitéer.

Använd insikterna för att skapa kundpaket som kombinerar visuell kvalitet med värde.

Dessa fynd möjliggör smartare inköpsstrategier, bättre marginaler och ett tydligare kundvärde vid produktutveckling och prissättning.

Självutvärdering
1. Vad har varit roligast i kunskapkontrollen?
Det roligaste tycker jag har varit är att jag lyckats skapa trevliga visualiseringar ur ett dataset. Jag började med matplotlib men övergick efter rekommendation från klasskamrat till plotly vilket kändes mycket enklare och graferna blev interaktiva och snyggare. Streamlit har också varit roligt att leka med. Kul hur man med så lite kod kan uppnå så mycket.

2. Vilket betyg anser du att du ska ha och varför?
Jag anser att jag har jobbat hårt efter bästa förmåga och jag har lärt mig väldigt mycket på ganska kort tid. Mitt arbete är i mitt tycke väldgjort och genomtänkt. Koden fungerar bra och resultatet känns relevant till målet jag satt upp. Jag som person är verkligen ingen som latar mig eller struntar i arbetsuppgifter och deadlines. Jag har jobbat på kontor sedan 13 år tillbaka och har bra dagsrutiner och hög arbetsmoral.
Men eftersom jag är 3-barns far och har haft lite stökigt privat dom senaste veckorna tycker jag att det jag presterat och den kunskap jag fått och med åtanke till den tid jag haft **ändå** bör visa på ett betyg **'Väl Godkänt'.**

3. Vad har varit mest utmanande i arbetet och hur har du hanterat det?
Det mest utmanande har varit att lära sig de tekniska verktygen samtidigt som jag försökt förstå hur man gör en bra analys. Det har tagit tid att få kläm på hur man använder Pandas och Plotly, och samtidigt tänka vilken data jag faktiskt vill analysera och presentera samt tillvägagångssätt för detta. Jag har jobbat hårt, blivit en del sena kvällar och nätter men det har varit roligt och lärt mig mycket längs vägen.
